API docs available here: https://developers.themoviedb.org/3

In [ ]:
# TODO

# Films with no budget information have budget=0. But we're not adjusting
# profit based on that, so it looks like they're profitable but we only
# have their box office. Need to adjust the profit to take account of that.

# Initialise

In [1]:
import pandas as pd
# import requests
# import numpy as np
# import config
# api_key = config.tmdb_key
# omdb_key = config.omdb_key

import json
import dill
import plotly.express as px
# import cpi
%config InlineBackend.figure_format ='retina'

import movies
import importlib

In [23]:
cpi.update()

In [207]:
importlib.reload(movies)

<module 'movies' from '/Users/nickydean83/Google Drive/Analytics/movie-stats/movies.py'>

In [48]:
%%capture
from tqdm import tqdm_notebook as tqdm
tqdm().pandas()

In [ ]:
# Request for a specific movie:
# requests.get('https://api.themoviedb.org/3/movie/'
#                                + '10994' 
#                                + '?api_key=' + api_key
#                                + '&language=en-US').json()

# example = requests.get('https://api.themoviedb.org/3/movie/'
#                                + '239459' 
#                                + '?api_key=' + api_key
#                                + '&language=en-US'
#                                + '&append_to_response=credits').json()

# Get 1980s films

get_films_data will pull all the films between two dates from TMDb. It will then look for those that have no budget or revenue information and scrape IMDb for it. The output in the end combines the two databases.

Note that we may not be successfully capturing all the IMDb data for some reason. May want to look into this later, as it's producing a lot of NaNs but it's not obvious why. Might have to inspect the webpage closely to see if the mark up is different or (easier) try re-running the IMDb part of the code to see if they can be pulled again.

In [636]:
df_1980s = movies.get_films_data('1980-01-01', '1989-12-31')

Get missing budget and revenue data from IMDb.
No. of queries to make =  3
Getting results from IMDb...


## OMDb analysis

What about adding more critical information? OMDb offers Metascore, Rotten Tomatoes and IMDb scores. Why not query that for the IMDb IDs we've extracted to gather these scores and add to our data? Note: OMDb has a maximum of 1,000 requests a day.

Get all the available OMBd data today. (Limited to 1,000 queries per day.)

In [116]:
omdb_1980s = get_omdb_data(df_1980s.sort_values('revenue_adj', ascending=False)[
    ['title', 'imdb_id', 'vote_average', 'revenue_adj', 'profit_adj']
    ])

Merge the scores information with the main dataframe. Determine which films have no ratings data (because of query limits at OMDb). We can search for those on another day so we'll store it as a json file for now.

In [641]:
df_1980s = df_1980s.merge(
    omdb_1980s[['imdbID', 'IMdb_score', 'Metacritic_score', 'RT_score']],
    left_on='imdb_id', right_on='imdbID', how='left')

In [659]:
missing_from_omdb_1980s = df_1980s[df_1980s['imdbID'].isna()][['title', 'imdb_id']]

In [661]:
# Save the missing OMDb data to json.
missing_from_omdb_1980s.to_json('data/missing_from_omdb_1980s.json', orient='records')

In [473]:
# Search for the missing OMDb data.
y = get_omdb_data(missing_from_omdb[
    ['title', 'imdb_id', 'vote_average', 'revenue_adj', 'profit_adj']
    ])

## Store results

In [658]:
df_1980s.to_json('data/df_1980s.json', orient='records')

In [657]:
with open('pickles/df_1980s.pkl', 'wb') as file:
    dill.dump(df_1980s, file)

Unpickle result with the following:

In [8]:
with open('pickles/df_1980s.pkl', 'rb') as file:
    df_1980s = dill.load(file)

## Plot some results

In [591]:
fig = px.scatter(data_1980s, x='Metacritic_score', y='RT_score', color='profit_adj', hover_name='title')
fig.show()

# Get 1990s films

In [18]:
df_1990s = movies.get_films_data('1990-01-01', '1999-12-31')

Get list of films.


Get details for each film.


Get missing budget and revenue data from IMDb.
Getting results from IMDb...


Fill in missing budget and revenue data with IMDb data.
Get release date information.
Adjust financial data for inflation.
Done.


In [527]:
omdb_1990s = get_omdb_data(df_1990s)

In [545]:
with open('data/omdb_1990s.json', 'w') as fout:
    json.dump(omdb_1990s, fout)

In [549]:
omdb_1990s_df = pd.DataFrame(omdb_1990s)

In [22]:
omdb_1990s_df

Actors  \
0    Tim Robbins, Morgan Freeman, Bob Gunton, Willi...   
1    Liam Neeson, Ben Kingsley, Ralph Fiennes, Caro...   
2    Tom Hanks, David Morse, Bonnie Hunt, Michael C...   
3    Tim Roth, Amanda Plummer, Laura Lovelace, John...   
4    Roberto Benigni, Nicoletta Braschi, Giorgio Ca...   
5    Tom Hanks, Rebecca Williams, Sally Field, Mich...   
6    Robert De Niro, Ray Liotta, Joe Pesci, Lorrain...   
7    Edward Norton, Brad Pitt, Meat Loaf, Zach Grenier   
8    Edward Norton, Edward Furlong, Beverly D'Angel...   
9    Tim Roth, Pruitt Taylor Vince, Mélanie Thierry...   
10   Jean Reno, Gary Oldman, Natalie Portman, Danny...   
11   Morgan Freeman, Andrew Kevin Walker, Daniel Za...   
12   Jodie Foster, Lawrence A. Bonney, Kasi Lemmons...   
13   Rowan Atkinson, Matthew Broderick, Niketa Cala...   
14   Stephen Baldwin, Gabriel Byrne, Benicio Del To...   
15   Mihály Vig, Putyi Horváth, László feLugossy, É...   
16   Junko Iwao, Rica Matsumoto, Shinpachi Tsuji, M...   
17   Jason Flemyng, Dexter Fletcher, Nick Moran, Ja...   
18   Tom Hanks, Tom Sizemore, Edward Burns, Barry P...   
19   Keanu Reeves, Laurence Fishburne, Carrie-Anne ...   
20   Matt Damon, Ben Affleck, Stellan Skarsgård, Jo...   
21   Brigitte Lin, Tony Chiu-Wai Leung, Faye Wong, ...   
22   Irène Jacob, Jean-Louis Trintignant, Frédériqu...   
23   Jim Carrey, Laura Linney, Noah Emmerich, Natas...   
24   Vincent Cassel, Hubert Koundé, Saïd Taghmaoui,...   
25   Kevin Spacey, Annette Bening, Thora Birch, Wes...   
26   Fernanda Montenegro, Marília Pêra, Vinícius de...   
27         Leslie Cheung, Fengyi Zhang, Li Gong, Qi Lü   
28   Robert De Niro, Sharon Stone, Joe Pesci, James...   
29   Mohammad Amir Naji, Amir Farrokh Hashemian, Ba...   
..                                                 ...   
878  Kimberly Deauna Adams, Vinny Argiro, Sean Asti...   
879  Robert De Niro, Kenneth Branagh, Tom Hulce, He...   
880  Virginia Madsen, Tony Todd, Xander Berkeley, K...   
881  River Phoenix, Samantha Mathis, Dermot Mulrone...   
882  Macaulay Culkin, Elijah Wood, Wendy Crewson, D...   
883  Aishwarya Rai Bachchan, Salman Khan, Ajay Devg...   
884  Tim Allen, Judge Reinhold, Wendy Crewson, Eric...   
885  Aidan Quinn, Kate Beckinsale, Anthony Andrews,...   
886  Sigourney Weaver, Charles S. Dutton, Charles D...   
887  Sylvester Stallone, John Lithgow, Michael Rook...   
888  Hedy Burress, Angelina Jolie, Jenny Lewis, Jen...   
889  John Travolta, Kyra Sedgwick, Forest Whitaker,...   
890  Gene Hackman, Mary Elizabeth Mastrantonio, Col...   
891  Bill Pullman, Ben Stiller, Ryan O'Neal, Kim Di...   
892  Nathan Lane, Lee Evans, Vicki Lewis, Maury Cha...   
893  Robbie Coltrane, Whoopi Goldberg, Ben Kingsley...   
894  Mary-Kate Olsen, Ashley Olsen, Cloris Leachman...   
895  Kathleen Turner, Dennis Quaid, Fiona Shaw, Sta...   
896  Jeff Bridges, Caroline Goodall, John Savage, S...   
897  Christopher Reid, Christopher Martin, Andre Ro...   
898  Harvey Keitel, Jason Salkey, Peter O'Toole, La...   
899  Charlie Sheen, Kiefer Sutherland, Chris O'Donn...   
900  James Woods, Melanie Griffith, Vincent Karthei...   
901  Kevin Bacon, Matt Dillon, Neve Campbell, There...   
902  Peter Riegert, Chazz Palminteri, Joey Travolta...   
903  Arnold Schwarzenegger, F. Murray Abraham, Art ...   
904  John Travolta, Robert Duvall, Tony Shalhoub, W...   
905  Kaelynn Craddick, Sara Craddick, Kate Capshaw,...   
906  Robert De Niro, Annette Bening, George Wendt, ...   
907  Phillip Glasser, James Stewart, Erica Yohn, Ca...   

                                                Awards     BoxOffice  \
0    Nominated for 7 Oscars. Another 19 wins & 32 n...           N/A   
1      Won 7 Oscars. Another 82 wins & 49 nominations.           N/A   
2    Nominated for 4 Oscars. Another 15 wins & 32 n...           N/A   
3       Won 1 Oscar. Another 62 wins & 69 nominations.           N/A   
4      Won 3 Oscars. Another 66 wins & 51 nominations.           N/A   
5      Won 6 Oscars

In [26]:
df_1990s = df_1990s.merge(
    omdb_1990s_df[['imdbID', 'Title', 'IMdb_score', 'Metacritic_score', 'RT_score']],
    left_on='imdb_id', right_on='imdbID', how='left').drop(columns=['Title'])

In [662]:
missing_from_omdb_1990s = data_1990s[data_1990s['imdbID'].isna()][['title', 'imdb_id']]

In [663]:
# Store the missing OMDb data as a json file.
missing_from_omdb_1990s.to_json('data/missing_from_omdb_1990s.json', orient='records')

In [559]:
fig = px.scatter(data_1990s, x='Metacritic_score', y='RT_score', color='profit_adj', hover_name='title')
fig.show()

## Pickle result

In [29]:
with open('pickles/df_1990s.pkl', 'wb') as file:
    dill.dump(df_1990s, file)

Unpickle result with the following:

In [9]:
with open('pickles/df_1990s.pkl', 'rb') as file:
    df_1990s = dill.load(file)

## Plot some results

In [312]:
df_1990s.columns

Index(['budget', 'credits', 'genres', 'id', 'original_language', 'popularity',
       'production_companies', 'production_countries', 'release_date',
       'revenue', 'runtime', 'spoken_languages', 'status', 'title',
       'vote_average', 'vote_count', 'year', 'decade', 'budget_adj',
       'revenue_adj', 'profit', 'profit_adj', 'budget_bin', 'budget_adj_bin'],
      dtype='object')

In [572]:
fig = px.scatter(df_1990s[df_1990s['budget']>0], x='budget', y='vote_average', hover_name='title')
fig.show()

In [573]:
fig = px.scatter(data_1990s[data_1990s['budget']>0], x='budget', y='vote_average', hover_name='title')
fig.show()

In [ ]:
fig = px.scatter(df_1990s[df_1990s['budget']>0], x='budget', y='revenue', color='year', hover_name='title')
fig.show()

In [ ]:
fig = px.box(df_1990s[df_1990s['budget']>0], x='year', y='budget')
fig.show()

In [ ]:
fig = px.histogram(df_1990s[df_1990s['vote_count']<=100], x='vote_count', nbins=100, color='title')
fig.show()

# Get 2000s

In [593]:
df_2000s = movies.get_films_data('2000-01-01', '2009-12-31')

Couldn't get film 8884
Couldn't get film 27374


Get missing budget and revenue data from IMDb.
No. of queries to make =  7
Getting results from IMDb...


In [594]:
df_2000s

budget                                            credits  \
0     185000000.0  {'cast': [{'cast_id': 35, 'character': 'Bruce ...   
1      94000000.0  {'cast': [{'cast_id': 12, 'character': 'Frodo ...   
2       3300000.0  {'cast': [{'cast_id': 34, 'character': 'Buscap...   
3      24000000.0  {'cast': [{'cast_id': 35, 'character': 'Sofî (...   
4      35000000.0  {'cast': [{'cast_id': 8, 'character': 'Wladysl...   
5      93000000.0  {'cast': [{'cast_id': 28, 'character': 'Frodo ...   
6      79000000.0  {'cast': [{'cast_id': 13, 'character': 'Frodo ...   
7       3000000.0  {'cast': [{'cast_id': 13, 'character': 'Oh Dae...   
8       9000000.0  {'cast': [{'cast_id': 4, 'character': 'Leonard...   
9      40000000.0  {'cast': [{'cast_id': 11, 'character': 'Robert...   
10            0.0  {'cast': [{'cast_id': 1, 'character': 'Himself...   
11     70000000.0  {'cast': [{'cast_id': 3, 'character': 'First L...   
12     90000000.0  {'cast': [{'cast_id': 2, 'character': 'William...   
13    103000000.0  {'cast': [{'cast_id': 8, 'character': 'Maximus...   
14     25000000.0  {'cast': [{'cast_id': 2, 'character': 'Daniel ...   
15            0.0  {'cast': [{'cast_id': 20, 'character': 'Chow M...   
16      5000000.0  {'cast': [{'cast_id': 1, 'character': 'Mr. Kim...   
17     20000000.0  {'cast': [{'cast_id': 5, 'character': 'Joel Ba...   
18      2000000.0  {'cast': [{'cast_id': 7, 'character': 'Christa...   
19      4000000.0  {'cast': [{'cast_id': 12, 'character': 'Capitã...   
20     16000000.0  {'cast': [{'cast_id': 1, 'character': 'Parker ...   
21      2600000.0  {'cast': [{'cast_id': 2, 'character': 'Ishaan ...   
22    180000000.0  {'cast': [{'cast_id': 12, 'character': 'WALL·E...   
23            0.0  {'cast': [{'cast_id': 3, 'character': 'Himself...   
24     33000000.0  {'cast': [{'cast_id': 1, 'character': 'Walt Ko...   
25            0.0  {'cast': [{'cast_id': 2, 'character': 'Ma Dasa...   
26    130000000.0  {'cast': [{'cast_id': 1, 'character': 'Harry P...   
27     30000000.0  {'cast': [{'cast_id': 3, 'character': 'Beatrix...   
28      2000000.0  {'cast': [{'cast_id': 1, 'character': 'Benjamí...   
29      9000000.0  {'cast': [{'cast_id': 5, 'character': 'Rancho'...   
...           ...                                                ...   
3075          0.0  {'cast': [{'cast_id': 7, 'character': 'John', ...   
3076   13000000.0  {'cast': [{'cast_id': 12, 'character': 'Duncan...   
3077   30000000.0  {'cast': [{'cast_id': 14, 'character': 'Leonid...   
3078   10000000.0  {'cast': [{'cast_id': 1, 'character': 'Rayne',...   
3079          0.0  {'cast': [{'cast_id': 1, 'character': 'Carolin...   
3080   54000000.0  {'cast': [{'cast_id': 9, 'character': 'Larry G...   
3081          0.0  {'cast': [{'cast_id': 1, 'character': 'Santiag...   
3082   22000000.0  {'cast': [{'cast_id': 1, 'character': 'Billie ...   
3083    6000000.0  {'cast': [{'cast_id': 4, 'character': 'Becky',...   
3084    7000000.0  {'cast': [{'cast_id': 1, 'character': 'Det. Ra...   
3085   30000000.0  {'cast': [{'cast_id': 1, 'character': 'Jack Ca...   
3086   40000000.0  {'cast': [{'cast_id': 1, 'character': 'Detecti...   
3087          0.0  {'cast': [{'cast_id': 1, 'character': 'Katie P...   
3088          0.0  {'cast': [{'cast_id': 1, 'character': 'Allan B...   
3089   20000000.0  {'cast': [{'cast_id': 1, 'character': 'Edward'...   
3090   20000000.0  {'cast': [{'cast_id': 12, 'character': 'Edward...   
3091          0.0  {'cast': [{'cast_id': 1, 'character': 'Luc Cra...   
3092   25000000.0  {'cast': [{'cast_id': 5, 'character': 'Will', ...   
3093          0.0  {'cast': [{'cast_id': 1, 'character': 'Cristab...   
3094   44000000.0  {'cast': [{'cast_id': 11, 'character': 'Terl',...   
3095    7000000.0  {'cast': [{'cast_id': 1, 'character': 'Rudy', ...   
3096   12000000.0  {'cast': [{'cast_id': 1, 'character': 'Kelly',...   
3097    7500000.0  {'cast': [{'cast_id': 1, 'character': 'Ace Ven...   
3098          0.0  {'cast': [{'cast_id': 1, 'charac

## Pickle result

In [595]:
with open('pickles/df_2000s.pkl', 'wb') as file:
    dill.dump(df_2000s, file)

Unpickle result with the following:

In [10]:
with open('pickles/df_2000s.pkl', 'rb') as file:
    df_2000s = dill.load(file)

## Plot some results

In [276]:
highest_revenue = df_2000s.sort_values('revenue', ascending=False)[0:1000]

In [ ]:
fig = px.box(highest_revenue[highest_revenue['budget']>0], x='year', y='budget',
             hover_data=['title'], points='all')
fig.show()

In [ ]:
fig = px.scatter(df_2000s[df_2000s['budget']>0], x='budget', y='revenue', color='year', hover_name='title')
fig.show()

Number of films in budget categories over time?

In [ ]:
grouped = df_2000s.groupby(['year', 'budget_bin']).count()

In [ ]:
fig = px.line(grouped.reset_index(), x='year', y='id', color='budget_bin')
fig.show()

# Get 2010s

In [4]:
df_2010s = movies.get_films_data('2010-01-01', '2019-12-31')

Get list of films.


Get details for each film.


Get missing budget and revenue data from IMDb.
Getting results from IMDb...


Fill in missing budget and revenue data with IMDb data.
Get release date information.
Adjust financial data for inflation.
Done.


In [5]:
df_2010s

budget                                            credits  \
0      55000000.0  {'cast': [{'cast_id': 2, 'character': 'Arthur ...   
1      90000000.0  {'cast': [{'cast_id': 16, 'character': 'Miles ...   
2       3300000.0  {'cast': [{'cast_id': 5, 'character': 'Andrew ...   
3       4000000.0  {'cast': [{'cast_id': 6, 'character': 'Zain', ...   
4             0.0  {'cast': [{'cast_id': 23, 'character': 'Johann...   
5     356000000.0  {'cast': [{'cast_id': 55, 'character': 'Tony S...   
6     160000000.0  {'cast': [{'cast_id': 1, 'character': 'Dom Cob...   
7      23000000.0  {'cast': [{'cast_id': 2, 'character': 'Frank "...   
8       4000000.0  {'cast': [{'cast_id': 4, 'character': 'Elio Pe...   
9     300000000.0  {'cast': [{'cast_id': 1, 'character': 'Tony St...   
10    165000000.0  {'cast': [{'cast_id': 9, 'character': 'Joseph ...   
11     23000000.0  {'cast': [{'cast_id': 6, 'character': 'Starr C...   
12            0.0  {'cast': [{'cast_id': 6, 'character': 'Himself...   
13     13000000.0  {'cast': [{'cast_id': 6, 'character': 'Philipp...   
14            0.0  {'cast': [{'cast_id': 3, 'character': 'Ephraim...   
15     20000000.0  {'cast': [{'cast_id': 123, 'character': 'Auggi...   
16            0.0  {'cast': [{'cast_id': 11, 'character': 'Hana (...   
17    175000000.0  {'cast': [{'cast_id': 5, 'character': 'Miguel ...   
18            0.0  {'cast': [], 'crew': [{'credit_id': '5744d6b79...   
19     12000000.0  {'cast': [{'cast_id': 31, 'character': 'Young ...   
20     15000000.0  {'cast': [{'cast_id': 0, 'character': 'Mildred...   
21     17000000.0  {'cast': [{'cast_id': 2, 'character': 'Simon S...   
22     25000000.0  {'cast': [{'cast_id': 10, 'character': 'Eugeni...   
23      5000000.0  {'cast': [{'cast_id': 2, 'character': 'Stella ...   
24     49300000.0  {'cast': [{'cast_id': 5, 'character': 'Princes...   
25      6000000.0  {'cast': [{'cast_id': 2, 'character': 'Joy "Ma...   
26            0.0  {'cast': [{'cast_id': 2, 'character': 'Conor /...   
27     80000000.0  {'cast': [{'cast_id': 2, 'character': 'Teddy D...   
28      2700000.0  {'cast': [{'cast_id': 1, 'character': 'Leonard...   
29    125000000.0  {'cast': [{'cast_id': 6, 'character': 'Harry P...   
...           ...                                                ...   
3577          0.0  {'cast': [{'cast_id': 9, 'character': 'Sleepin...   
3578    4500000.0  {'cast': [{'cast_id': 1, 'character': 'Granger...   
3579          0.0  {'cast': [{'cast_id': 27, 'character': 'Scott'...   
3580          0.0  {'cast': [{'cast_id': 2, 'character': 'Adam', ...   
3581   10000000.0  {'cast': [{'cast_id': 2, 'character': 'Rayne',...   
3582          0.0  {'cast': [{'cast_id': 5, 'character': 'Jennife...   
3583     600000.0  {'cast': [{'cast_id': 2, 'character': 'Jill', ...   
3584    5000000.0  {'cast': [{'cast_id': 2, 'character': 'Lara Sl...   
3585          0.0  {'cast': [{'cast_id': 9, 'character': 'William...   
3586          0.0  {'cast': [{'cast_id': 1, 'character': 'Elias V...   
3587          0.0  {'cast': [{'cast_id': 1, 'character': 'Col. Ge...   
3588    1300000.0  {'cast': [{'cast_id': 1, 'character': 'Andy', ...   
3589          0.0  {'cast': [{'cast_id': 7, 'character': 'Dracula...   
3590          0.0  {'cast': [{'cast_id': 1, 'character': 'Lt. Tyl...   
3591          0.0  {'cast': [{'cast_id': 10, 'character': 'Jimmy ...   
3592    1500000.0  {'cast': [{'cast_id': 2, 'character': 'Alex Co...   
3593    6000000.0  {'cast': [{'cast_id': 4, 'character': 'McCormi...   
3594          0.0  {'cast': [{'cast_id': 12, 'character': 'Bella'...   
3595          0.0  {'cast': [{'cast_id': 1, 'character': 'Hayden ...   
3596     350000.0  {'cast': [{'cast_id': 3, 'character': 'Dr. Ros...   
3597          0.0  {'cast': [{'cast_id': 9, 'character': 'Troit',...   
3598    3000000.0  {'cast': [{'cast_id': 3, 'character': 'Jason F...   
3599          0.0  {'cast': [{'cast_id': 3, 'character': 'J.D.', ...   
3600          0.0  {'cast': [{'cast_id': 1, 'charac

Pickle result

In [6]:
with open('pickles/df_2010s.pkl', 'wb') as file:
    dill.dump(df_2010s, file)

Unpickle result with the following:

In [11]:
with open('pickles/df_2010s.pkl', 'rb') as file:
    df_2010s = dill.load(file)

In [5]:
df_2010s.columns

Index(['budget', 'credits', 'genres', 'id', 'original_language', 'popularity',
       'production_companies', 'production_countries', 'release_date',
       'revenue', 'runtime', 'spoken_languages', 'status', 'title',
       'vote_average', 'vote_count', 'year', 'decade', 'budget_adj',
       'revenue_adj', 'profit', 'profit_adj', 'budget_bin', 'budget_adj_bin'],
      dtype='object')

## Plot some results

In [ ]:
highest_revenue = df_2010s.sort_values('revenue', ascending=False)[0:1000]

In [ ]:
fig = px.box(highest_revenue[highest_revenue['budget']>0], x='year', y='budget',
             hover_data=['title'], points='all')
fig.show()

In [8]:
fig = px.scatter(df_2010s[df_2010s['budget']>0], x='budget', y='revenue', color='year', hover_name='title')
fig.show()

In [ ]:
grouped = df_2010s.groupby(['year', 'budget_bin']).count()

In [ ]:
fig = px.line(grouped.reset_index(), x='year', y='id', color='budget_bin')
fig.show()

In [17]:
df_2010s['profit_rank'] = df_2010s['profit_adj'].rank(ascending=False)

In [20]:
df_2010s[['title', 'profit_adj', 'profit_rank']].sort_values('profit_adj', ascending=False)[0:10]

title    profit_adj  profit_rank
4                                Avengers: Endgame  2.441801e+09          1.0
267                   Star Wars: The Force Awakens  1.931609e+09          2.0
10                          Avengers: Infinity War  1.746240e+09          3.0
1159                                Jurassic World  1.612175e+09          4.0
139                                   The Avengers  1.421327e+09          5.0
389                                      Furious 7  1.394497e+09          6.0
511                                  The Lion King  1.389677e+09          7.0
29    Harry Potter and the Deathly Hallows: Part 2  1.358578e+09          8.0
393                                         Frozen  1.211808e+09          9.0
346                        Avengers: Age of Ultron  1.192306e+09         10.0

In [21]:
fig = px.scatter(df_2010s[df_2010s['budget']>0].sort_values('profit_adj', ascending=False)[0:10],
                 x='vote_average', y='profit_rank', color='year', hover_name='title')
fig.show()

# Check all decades

Build all the decades of data...

In [134]:
all_films = pd.concat([df_1980s, df_1990s, df_2000s, df_2010s], axis=0, sort=False).reset_index(drop=True)

...or load the existing data.

In [131]:
with open('pickles/all_films.pkl', 'rb') as file:
    all_films = dill.load(file)

In [132]:
all_films.columns

Index(['title', 'budget', 'credits', 'genres', 'id', 'imdb_id',
       'original_language', 'popularity', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'vote_average', 'vote_count',
       'budget_imdb', 'revenue_imdb', 'year', 'decade', 'budget_adj',
       'revenue_adj', 'profit', 'profit_adj', 'budget_bin', 'budget_adj_bin',
       'imdbID', 'IMdb_score', 'Metacritic_score', 'RT_score'],
      dtype='object')

In [92]:
all_films = all_films[['title', 'budget', 'credits', 'genres', 'id', 'imdb_id', 'original_language',
       'popularity', 'production_companies', 'production_countries',
       'release_date', 'revenue', 'runtime', 'spoken_languages', 'status',
       'vote_average', 'vote_count', 'budget_imdb', 'revenue_imdb',
       'year', 'decade', 'budget_adj', 'revenue_adj', 'profit', 'profit_adj',
       'budget_bin', 'budget_adj_bin', 'imdbID', 'IMdb_score',
       'Metacritic_score', 'RT_score']]

In [94]:
all_films.shape

(9476, 31)

Get the data that don't have OMDb ratings information.

In [99]:
missing = all_films[all_films['imdbID'].isna()].sort_values('popularity', ascending=False)

In [100]:
omdb_new = movies.get_omdb_data(missing[0:1000][
    ['title', 'imdb_id', 'vote_average', 'revenue_adj', 'profit_adj']
    ])

In [101]:
len(omdb_new)

1000

In [102]:
omdb_new_df = pd.DataFrame(omdb_new)

Now we want to merge the existing and new OMDb data. Start by loading the saved data.

In [103]:
omdb = pd.read_json('data/omdb.json')
omdb_df = pd.DataFrame(omdb)

In [104]:
omdb_df[~omdb_df['Error'].isna()]

Actors Awards BoxOffice Country   DVD Director                  Error  \
3434   None   None      None    None  None     None  Something went wrong.   

     Genre  IMdb_score Language  ...  Runtime Title  Type Website Writer  \
3434  None         NaN     None  ...     None  None  None    None   None   

      Year imdbID imdbRating imdbVotes totalSeasons  
3434  None   None       None      None          NaN  

[1 rows x 30 columns]

Append the new dataframe to the old one.

In [105]:
omdb_df = omdb_df.append(omdb_new_df, ignore_index=True, sort=True)

In [106]:
omdb_df.drop_duplicates('imdbID', inplace=True)

In [107]:
omdb_df.shape

(5771, 30)

Save the missing OMDb data to json.

In [108]:
omdb_df.to_json('data/omdb.json', orient='records')

Now we want to add the ratings info to the rest of the records. Start by dropping the OMDb columns, then merge the newly extended OMDb dataframe onto it.

In [109]:
all_films.drop(columns=['IMdb_score',
       'Metacritic_score', 'RT_score', 'imdbID'], inplace=True)

all_films = all_films.merge(
    omdb_df[['imdbID', 'Title', 'IMdb_score', 'Metacritic_score', 'RT_score']],
    left_on='imdb_id', right_on='imdbID', how='left').drop(columns=['Title'])

In [110]:
all_films[all_films['budget']==0].shape

(2508, 31)

Pickle the result.

In [111]:
with open('pickles/all_films.pkl', 'wb') as file:
    dill.dump(all_films, file)

At last count, 2,508 films have no budget information, i.e. budget = 0. Total number of films in database is 9,476.

## Plot some data

In [112]:
fig = px.scatter(all_films.astype({'decade': 'category'}), 
                 x='Metacritic_score', y='profit_adj', 
                 color='decade', hover_name='title')
fig.update_xaxes(range=[0,100])
# fig.update_yaxes(range=[0,100])
fig.show()

In [113]:
fig = px.scatter(all_films.astype({'decade': 'category'}), 
                 x='Metacritic_score', y='IMdb_score', 
                 color='decade', hover_name='title')
fig.update_xaxes(range=[0,100])
fig.update_yaxes(range=[0,100])
fig.show()

In [61]:
fig = px.scatter(all_films.astype({'decade': 'category'}), 
                 x='Metacritic_score', y='RT_score', 
                 color='decade', hover_name='title',
                 color_discrete_sequence=px.colors.colorbrewer.Set1,
                 template='plotly_dark')

fig.update_traces(marker=dict(size=9,
                              line=dict(width=1)),
                  selector=dict(mode='markers'))

fig.update_xaxes(range=[-2,102])
fig.update_yaxes(range=[-2,102])

fig.update_xaxes(title_text='Metacritic score')
fig.update_yaxes(title_text='Rotten Tomatoes score')

fig.show()

In [114]:
fig = px.scatter(all_films.astype({'decade': 'category'}), 
                 x='Metacritic_score', y='RT_score', 
                 color='decade', hover_name='title',
                 color_discrete_sequence=px.colors.colorbrewer.Set1,
                 template='plotly_dark')

fig.update_traces(marker=dict(size=9,
                              line=dict(width=1)),
                  selector=dict(mode='markers'))

fig.update_xaxes(range=[-2,102])
fig.update_yaxes(range=[-2,102])

fig.update_xaxes(title_text='Metacritic score')
fig.update_yaxes(title_text='Rotten Tomatoes score')

fig.show()

In [25]:
# (all_films['budget_adj']/1e6).plot.hist(bins=100)

fig = px.histogram(all_films[(all_films['budget_adj']!=0) & (all_films['budget_adj']>=300e6)
                            ], x='budget_adj', nbins=200)
fig.show()

In [26]:
grouped = all_films.groupby(['year', 'budget_adj_bin']).count()

In [27]:
fig = px.line(grouped.reset_index(), x='year', y='id', color='budget_adj_bin')
fig.show()

In [87]:
fig = px.box(all_films[all_films['budget']>0], x='year', y='budget_adj')
fig.show()

In [88]:
fig = px.parallel_categories(all_films.dropna(subset=['budget_adj_bin']), 
                             dimensions=['budget_adj_bin', 'decade'])

fig.show()

# Extract genre info

## Pickle result

In [133]:
all_films.head()

title      budget  \
0  Once Upon a Time in America  20000000.0   
1              Cinema Paradiso   5000000.0   
2      The Empire Strikes Back  18000000.0   
3           Dead Poets Society  16400000.0   
4    The Man Who Planted Trees         0.0   

                                             credits  \
0  {'cast': [{'cast_id': 3, 'character': 'David '...   
1  {'cast': [{'cast_id': 8, 'character': 'Alfredo...   
2  {'cast': [{'cast_id': 7, 'character': 'Luke Sk...   
3  {'cast': [{'cast_id': 3, 'character': 'John Ke...   
4  {'cast': [{'cast_id': 2, 'character': 'Narrato...   

                                 genres     id    imdb_id original_language  \
0                        [Drama, Crime]    311  tt0087843                en   
1                      [Drama, Romance]  11216  tt0095765                it   
2  [Adventure, Action, Science Fiction]   1891  tt0080684                en   
3                               [Drama]    207  tt0097165                en   
4                    [Animation, Drama]  49565  tt0093488                fr   

   popularity                               production_companies  \
0      19.222  [{'id': 7965, 'logo_path': None, 'name': 'The ...   
1      12.876  [{'id': 67486, 'logo_path': '/lQrBjILcFLcPLZwV...   
2      20.094  [{'id': 1, 'logo_path': '/o86DbpburjxrqAzEDhXZ...   
3      22.543  [{'id': 9195, 'logo_path': '/ou5BUbtulr6tIt699...   
4       4.924  [{'id': 9115, 'logo_path': None, 'name': 'Soci...   

                                production_countries  ...    budget_adj  \
0  [{'iso_3166_1': 'US', 'name': 'United States o...  ...  4.833628e+07   
1            [{'iso_3166_1': 'IT', 'name': 'Italy'}]  ...  1.061314e+07   
2  [{'iso_3166_1': 'US', 'name': 'United States o...  ...  5.485347e+07   
3  [{'iso_3166_1': 'US', 'name': 'United States o...  ...  3.321093e+07   
4           [{'iso_3166_1': 'CA', 'name': 'Canada'}]  ...  0.000000e+00   

    revenue_adj       profit    profit_adj budget_bin  budget_adj_bin  \
0  1.280912e+07  -14700000.0 -3.552717e+07     10-30M          30-50M   
1  2.545117e+07    6990401.0  1.483803e+07       2-5M          10-30M   
2  1.640728e+09  520400000.0  1.585875e+09     10-30M         50-100M   
3  4.776300e+08  219460116.0  4.444191e+08     10-30M          30-50M   
4  0.000000e+00          0.0  0.000000e+00        NaN             NaN   

      imdbID  IMdb_score  Metacritic_score  RT_score  
0  tt0087843          84               NaN        86  
1  tt0095765          85                80        90  
2  tt0080684          87                82        95  
3  tt0097165          81                79        84  
4  tt0093488          86               NaN       NaN  

[5 rows x 31 columns]

In [126]:
all_films['genres'] = ["|".join(list_dict) for list_dict in all_films['genres']]

In [136]:
import numpy as np

In [167]:
def list_col_to_rows(df, list_col):
    new_df = pd.DataFrame(
        {col:np.repeat(df[col].values, df[list_col].str.len())
            for col in df.columns.drop(list_col)}
            ).assign(**{list_col:np.concatenate(df[list_col].values)})[df.columns]
    return new_df

In [138]:
lst_col = 'genres'

genres = pd.DataFrame(
    {col:np.repeat(all_films[col].values, df[lst_col].str.len())
        for col in all_films.columns.drop(lst_col)}
        ).assign(**{lst_col:np.concatenate(all_films[lst_col].values)})[all_films.columns]

In [82]:
genres = all_films['genres'].apply(pd.Series) \
    .merge(all_films, left_index = True, right_index = True) \
    .drop(columns=['genres']) \
    .melt(id_vars=['budget', 'credits', 'id', 'original_language', 'popularity',
       'production_companies', 'production_countries', 'release_date',
       'revenue', 'runtime', 'spoken_languages', 'status', 'title',
       'vote_average', 'vote_count', 'year', 'decade', 'budget_adj',
       'revenue_adj', 'profit', 'profit_adj', 'budget_bin', 'budget_adj_bin'], value_name='genre') \
    .drop(columns="variable") \
    .dropna(subset=['genre'])

In [141]:
genres.groupby(['year', 'genres'])['budget_adj'].sum().reset_index()

year           genres    budget_adj
0    1980           Action  6.204537e+08
1    1980        Adventure  4.326019e+08
2    1980        Animation  1.828449e+07
3    1980           Comedy  6.376929e+08
4    1980            Crime  2.078337e+08
5    1980            Drama  5.840374e+08
6    1980           Family  1.050048e+08
7    1980          Fantasy  9.723387e+07
8    1980          History  4.571155e+07
9    1980           Horror  3.496909e+08
10   1980            Music  2.498880e+08
11   1980          Mystery  1.103164e+08
12   1980          Romance  2.559829e+08
13   1980  Science Fiction  5.105944e+08
14   1980         Thriller  3.861075e+08
15   1980              War  6.856716e+07
16   1980          Western  1.645604e+08
17   1981           Action  4.450312e+08
18   1981        Adventure  3.853622e+08
19   1981        Animation  5.884025e+07
20   1981           Comedy  2.711348e+08
21   1981            Crime  1.148131e+08
22   1981            Drama  6.243680e+08
23   1981           Family  2.127089e+08
24   1981          Fantasy  1.610510e+08
25   1981          History  2.555269e+08
26   1981           Horror  2.553529e+08
27   1981            Music  6.712762e+07
28   1981          Mystery  1.285922e+08
29   1981          Romance  2.161620e+08
..    ...              ...           ...
644  2018           Comedy  2.102428e+09
645  2018            Crime  7.129000e+08
646  2018            Drama  1.484390e+09
647  2018           Family  1.566050e+09
648  2018          Fantasy  1.853550e+09
649  2018          History  3.360000e+08
650  2018           Horror  5.526255e+08
651  2018            Music  1.564405e+08
652  2018          Mystery  2.847000e+08
653  2018          Romance  3.654000e+08
654  2018  Science Fiction  2.497000e+09
655  2018         Thriller  1.239350e+09
656  2018              War  7.300000e+07
657  2018          Western  0.000000e+00
658  2019           Action  2.784100e+09
659  2019        Adventure  3.138000e+09
660  2019        Animation  1.159000e+09
661  2019           Comedy  1.787500e+09
662  2019            Crime  1.945000e+08
663  2019            Drama  9.431000e+08
664  2019           Family  1.464000e+09
665  2019          Fantasy  1.380600e+09
666  2019          History  2.276000e+08
667  2019           Horror  3.330000e+08
668  2019            Music  1.260000e+08
669  2019          Mystery  1.045000e+08
670  2019          Romance  3.506000e+08
671  2019  Science Fiction  1.803000e+09
672  2019         Thriller  8.460000e+08
673  2019              War  1.200000e+08

[674 rows x 3 columns]

In [145]:
fig = px.line(genres.groupby(['year', 'genres'])['profit_adj'].sum().reset_index(),
              x='year', y='profit_adj', color='genres')
fig.show()

In [148]:
fig = px.scatter(genres[(genres['profit_adj']<0) & (genres['revenue'] !=0)], 
                 x='vote_average', y='profit_adj',
                 hover_data=['title','revenue'],
                 color='genres', size='budget')
fig.show()

# Extract directors

Syntax for list comprehension with an if condition:
[f(x) for x in sequence if condition]

For embedded lists:
[[x['name'] for x in list_dict] for list_dict in all_films['genres']]

In [230]:
all_films.columns

Index(['title', 'budget', 'credits', 'genres', 'id', 'imdb_id',
       'original_language', 'popularity', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'vote_average', 'vote_count',
       'budget_imdb', 'revenue_imdb', 'year', 'decade', 'budget_adj',
       'revenue_adj', 'profit', 'profit_adj', 'budget_bin', 'budget_adj_bin',
       'imdbID', 'IMdb_score', 'Metacritic_score', 'RT_score'],
      dtype='object')

In [237]:
directors = pd.Series(
    [[x['name'] for x in crew_list if x['job'] == 'Director'] 
         for crew_list in [x['crew'] for x in all_films['credits']]
    ], name='director').to_frame()

directors_gender = pd.Series(
    [[x['gender'] for x in crew_list if x['job'] == 'Director'] 
        for crew_list in [x['crew'] for x in all_films['credits']]
    ], name='gender').to_frame()

directors_df = list_col_to_rows(directors \
                 .merge(all_films, left_index = True, right_index = True), 
                 'director')

directors_gender_df = list_col_to_rows(directors_gender, 'gender')

directors_gender_df['gender'].replace({0: 'Unspecified', 
                                       1: 'Female', 
                                       2: 'Male'}, 
                                      inplace=True)

directors_df = directors_gender_df.merge(directors_df, 
                                         left_index = True, right_index = True)

In [211]:
directors_rank = movies.rankings(directors_df, director=True)

directors_rank_decades = movies.rankings_decades(directors_df, director=True)

directors_rank_years = movies.rankings_years(directors_df, director=True)

In [212]:
directors_rank_decades[(directors_rank_decades['decade']==2010) 
                       & (directors_rank_decades['gender'] == 'Female')
                      ].sort_values('profit_adj', ascending=False)

director  decade  films    profit_adj    budget_adj  \
1467            Jennifer Lee    2010      2  1.211808e+09  1.616867e+08   
578      Jennifer Yuh Nelson    2010      3  9.763953e+08  3.531561e+08   
771               Anna Boden    2010      3  9.640812e+08  1.718070e+08   
3337           Patty Jenkins    2010      1  6.892811e+08  1.526393e+08   
3269      Sam Taylor-Johnson    2010      1  5.625730e+08  4.237789e+07   
4891          Brenda Chapman    2010      1  3.871515e+08  2.023345e+08   
798          Elizabeth Banks    2010      3  3.132044e+08  3.719144e+07   
3426           Thea Sharrock    2010      1  1.966373e+08  2.092497e+07   
1684               Trish Sie    2010      2  1.868018e+08  9.383083e+07   
2903          Sharon Maguire    2010      1  1.851362e+08  3.661870e+07   
2760            Nancy Meyers    2010      1  1.690503e+08  3.708065e+07   
840          Lorene Scafaria    2010      3  1.293261e+08  3.428500e+07   
3623          Phyllida Lloyd    2010      1  1.138177e+08  1.451234e+07   
1297     Julie Anne Robinson    2010      2  9.914046e+07  4.374801e+07   
5771            Frankie Chen    2010      1  8.885318e+07  0.000000e+00   
768           Angelina Jolie    2010      3  8.694966e+07  9.070362e+07   
1214         Kathryn Bigelow    2010      2  8.388783e+07  7.857845e+07   
1728            Ava DuVernay    2010      2  7.930402e+07  1.242141e+08   
669            Susanna White    2010      3  7.754512e+07  4.030499e+07   
5111              Kay Cannon    2010      1  7.267479e+07  2.100000e+07   
5638            Greta Gerwig    2010      1  6.849127e+07  1.024425e+07   
1289           Nadine Labaki    2010      2  6.835456e+07  5.004700e+06   
498          Patricia Riggen    2010      3  6.056195e+07  4.322616e+07   
5487         Kimberly Peirce    2010      1  5.647640e+07  3.233734e+07   
5897              Jenny Gage    2010      1  5.549759e+07  1.400000e+07   
636      Catherine Hardwicke    2010      3  5.255645e+07  6.220939e+07   
1278               Niki Caro    2010      2  5.180705e+07  2.048850e+07   
3139           Roxann Dawson    2010      1  5.044436e+07  0.000000e+00   
4485           Anna Foerster    2010      1  4.822507e+07  3.661870e+07   
1614            Jodie Foster    2010      2  4.698883e+07  5.169172e+07   
...                      ...     ...    ...           ...           ...   
1296             Julie Delpy    2010      2 -6.915280e+06  8.749601e+06   
3300          Sophie Barthes    2010      1 -7.248174e+06  7.945854e+06   
5095         Karen Moncrieff    2010      1 -7.276332e+06  7.545380e+06   
55         Lauren Montgomery    2010      6 -7.937667e+06  7.937667e+06   
4127       Floria Sigismondi    2010      1 -8.065822e+06  1.151571e+07   
4025           Claudia Llosa    2010      1 -8.429329e+06  8.485638e+06   
4411           Andrea Arnold    2010      1 -8.818015e+06  8.930670e+06   
2450             Nora Twomey    2010      1 -9.309582e+06  9.629593e+06   
1366         Marjane Satrapi    2010      2 -9.576496e+06  1.339601e+07   
4376         Angela Robinson    2010      1 -9.645206e+06  1.126867e+07   
5497             Kim Farrant    2010      1 -1.057596e+07  1.059447e+07   
5524           Liz W. Garcia    2010      1 -1.077911e+07  1.077911e+07   
1693           Valerie Faris    2010      2 -1.142942e+07  3.436022e+07   
5900         Jericca Cleland    2010      1 -1.169567e+07  2.092497e+07   
5404              Mari Okada    2010      1 -1.245047e+07  1.700000e+07   
4427       Andrea Di Stefano    2010      1 -1.404550e+07  1.803198e+07   
4806          Cate Shortland    2010      1 -1.515973e+07  1.536637e+07   
5308                 Madonna    2010      1 -1.577554e+07  1.674501e+07   
1768         Ami Canaan Mann    2010      2 -1.694290e+07  1.803198e+07   
4400          Amy Heckerling    2010      1 -1.739776e+07  1.749920e+07   
1703           Anne Fontaine    2010      2 -1.900593e+07  2.729359e+07   
2421          Nicole Kassell    2010      1 -

In [68]:
directors_rank.sort_values('profit_adj', ascending=False)

director  films    profit_adj    budget_adj  average_profit  \
2         Steven Spielberg     27  1.297948e+10  2.537006e+09    4.807216e+08   
180          James Cameron      8  7.369333e+09  1.173199e+09    9.211666e+08   
41           Peter Jackson     14  6.503993e+09  1.585225e+09    4.645709e+08   
50             Michael Bay     13  5.873935e+09  2.004157e+09    4.518412e+08   
342          Anthony Russo      6  5.820770e+09  1.156355e+09    9.701284e+08   
362              Joe Russo      6  5.820770e+09  1.156355e+09    9.701284e+08   
11         Robert Zemeckis     18  5.375382e+09  1.745945e+09    2.986323e+08   
253            David Yates      7  5.221491e+09  1.478361e+09    7.459273e+08   
36          Chris Columbus     14  5.165203e+09  9.546548e+08    3.689430e+08   
117      Christopher Nolan     10  4.126942e+09  1.270926e+09    4.126942e+08   
3               Ron Howard     24  3.989321e+09  2.067929e+09    1.662217e+08   
6               Tim Burton     21  3.972411e+09  1.869035e+09    1.891624e+08   
730          Pierre Coffin      4  3.632801e+09  3.217327e+08    9.082002e+08   
44         Roland Emmerich     14  3.581652e+09  1.677527e+09    2.558323e+08   
130            Jon Favreau      9  3.468289e+09  1.164653e+09    3.853654e+08   
91               James Wan     10  3.416375e+09  4.743129e+08    3.416375e+08   
121         Gore Verbinski     10  3.045081e+09  1.503032e+09    3.045081e+08   
42               Sam Raimi     14  2.995376e+09  1.278274e+09    2.139554e+08   
1           Clint Eastwood     31  2.978532e+09  1.500085e+09    9.608169e+07   
68      M. Night Shyamalan     11  2.935642e+09  8.606910e+08    2.668765e+08   
251        Carlos Saldanha      7  2.931273e+09  6.388102e+08    4.187533e+08   
833           George Lucas      3  2.906379e+09  4.861206e+08    9.687931e+08   
196              Brad Bird      7  2.896049e+09  9.726287e+08    4.137213e+08   
219       Francis Lawrence      7  2.820778e+09  8.638853e+08    4.029683e+08   
559            J.J. Abrams      4  2.815154e+09  8.267723e+08    7.037884e+08   
88            Bryan Singer     10  2.802507e+09  1.428316e+09    2.802507e+08   
402           Chris Renaud      5  2.728509e+09  3.964073e+08    5.457018e+08   
46            Ivan Reitman     14  2.709006e+09  7.499508e+08    1.935004e+08   
148            Bill Condon      9  2.672930e+09  6.118573e+08    2.969922e+08   
4             Ridley Scott     23  2.633348e+09  2.196080e+09    1.144934e+08   
...                    ...    ...           ...           ...             ...   
365            Gregg Araki      5 -8.574191e+07  8.893877e+07   -1.714838e+07   
4270           Joby Harold      1 -8.674477e+07  1.041526e+08   -8.674477e+07   
94       Charles Grosvenor     10 -8.680356e+07  9.824162e+07   -8.680356e+06   
1643           Tim Robbins      2 -8.843130e+07  1.613074e+08   -4.421565e+07   
4104          Hugh Johnson      1 -8.852959e+07  1.055071e+08   -8.852959e+07   
1081          Luc Dardenne      3 -8.923204e+07  9.785963e+07   -2.974401e+07   
901   Jean-Pierre Dardenne      3 -8.923204e+07  9.785963e+07   -2.974401e+07   
2870    David A. Armstrong      1 -8.946218e+07  8.946664e+07   -8.946218e+07   
3058            Elaine May      1 -8.979909e+07  1.215747e+08   -8.979909e+07   
1996       Moustapha Akkad      1 -9.254218e+07  9.668586e+07   -9.254218e+07   
1370          Noriyuki Abe      2 -9.509214e+07  1.050111e+08   -4.754607e+07   
144           Roland Joffé      9 -9.568385e+07  2.780019e+08   -1.063154e+07   
906         Jeannot Szwarc      3 -9.732548e+07  2.168157e+08   -3.244183e+07   
4004              Léa Pool      1 -9.868903e+07  9.925178e+07   -9.868903e+07   
128           Robert Vince      9 -9.992388e+07  1.002527e+08   -1.110265e+07   
2162       Stuart Margolin      1 -1.042659e+08  1.042659e+08   -1.042659e+08   
2058        Michael Thelin      1 -1.046184e+08  1.046249e+08   -1.046184e+08   
631            Gordon Chan      4 -1.047555e+08  

In [69]:
directors_rank.sort_values('films', ascending=False)

director  films    profit_adj    budget_adj  average_profit  \
0             Woody Allen     38  7.746661e+08  6.771690e+08    2.038595e+07   
1          Clint Eastwood     31  2.978532e+09  1.500085e+09    9.608169e+07   
2        Steven Spielberg     27  1.297948e+10  2.537006e+09    4.807216e+08   
3              Ron Howard     24  3.989321e+09  2.067929e+09    1.662217e+08   
4            Ridley Scott     23  2.633348e+09  2.196080e+09    1.144934e+08   
5       Steven Soderbergh     22  1.993880e+09  1.005650e+09    9.063090e+07   
6              Tim Burton     21  3.972411e+09  1.869035e+09    1.891624e+08   
7         Martin Scorsese     20  1.347483e+09  1.382141e+09    6.737414e+07   
8         Joel Schumacher     20  1.513252e+09  1.054091e+09    7.566260e+07   
9              Wes Craven     19  8.957053e+08  4.488494e+08    4.714239e+07   
14             Rob Reiner     18  9.260545e+08  7.335158e+08    5.144747e+07   
16              Joel Coen     18  1.015897e+09  4.834178e+08    5.643873e+07   
15       Robert Rodriguez     18  1.136863e+09  7.337260e+08    6.315906e+07   
11        Robert Zemeckis     18  5.375382e+09  1.745945e+09    2.986323e+08   
13           Oliver Stone     18  1.181358e+09  1.025894e+09    6.563098e+07   
12        Kunihiko Yuyama     18  1.256608e+09  4.065476e+08    6.981157e+07   
10         Barry Levinson     18  1.661160e+09  7.648154e+08    9.228665e+07   
17           Renny Harlin     17  5.782089e+08  1.205237e+09    3.401229e+07   
18          Stephen Herek     17  5.975313e+08  5.282053e+08    3.514890e+07   
19             Luc Besson     17  3.558709e+08  9.758101e+08    2.093358e+07   
20        Pedro Almodóvar     17  2.704107e+08  1.538400e+08    1.590651e+07   
25        Lasse Hallström     16  7.224228e+08  5.267208e+08    4.515142e+07   
26             Tony Scott     16  2.387590e+09  1.247306e+09    1.492244e+08   
24      Richard Linklater     16  2.486984e+08  2.220444e+08    1.554365e+07   
22            Walter Hill     16  1.211895e+08  8.402365e+08    7.574346e+06   
21          Michael Apted     16  1.230692e+09  6.878811e+08    7.691823e+07   
23            Tyler Perry     16  6.232166e+08  2.920386e+08    3.895104e+07   
27         John Carpenter     15  1.900674e+08  4.478066e+08    1.267116e+07   
28           Gus Van Sant     15  3.735884e+08  3.105874e+08    2.490589e+07   
29         Stephen Frears     15  3.038532e+08  3.602403e+08    2.025688e+07   
...                   ...    ...           ...           ...             ...   
2764       Robert Englund      1  5.849789e+06  4.245258e+05    5.849789e+06   
2754      Robert McKimson      1  2.038781e+05  0.000000e+00    2.038781e+05   
2765     Robert Greenwald      1  7.531976e+06  6.094830e+07    7.531976e+06   
2766    Robert Guédiguian      1 -1.030019e+07  1.170460e+07   -1.030019e+07   
2767         Robert Heath      1  2.738689e+06  0.000000e+00    2.738689e+06   
2768       Robert Hiltzik      1  2.685030e+07  8.824041e+05    2.685030e+07   
2769       Robert Houston      1 -5.485347e+07  5.485347e+07   -5.485347e+07   
2770  Robert J. Rosenthal      1  4.397044e+07  0.000000e+00    4.397044e+07   
2771      Robert K. Weiss      1  1.212864e+06  0.000000e+00    1.212864e+06   
2755        Robert Lorenz      1  3.167699e+07  2.187400e+07    3.167699e+07   
2753        Rodney Ascher      1  7.606314e+03  0.000000e+00    7.606314e+03   
2735         Robert Young      1  1.467726e+07  0.000000e+00    1.467726e+07   
2743        Robert Walker      1  2.052497e+08  1.364712e+08    2.052497e+08   
2736       Robert Moresco      1 -4.944571e+06  5.000000e+06   -4.944571e+06   
2737        Robert Morgan      1  7.606314e+03  0.000000e+00    7.606314e+03   
2738      Robert Mulligan      1  5.261449e+06  0.000000e+00    5.261449e+06   
2739         Robert Olsen      1  3.635923e+04  0.000000e+00    3.635923e+04   
2740         Robert Shaye      1  3.305930e+07  0.000000e+00    3.305930e+07   
2741   Robert Ste

In [215]:
fig = px.scatter(directors_rank_years[directors_rank_years['profit_rank']<=50], 
                 x='year', y='profit_rank',
                 hover_data=['director'], color='gender', size='profit_adj',
                 range_y=[51,-1], #color_discrete_sequence=px.colors.sequential.Cividis
                )
fig.show()

# Extract cast

In [71]:
actors = pd.Series([[x['name'] for x in cast_list] 
              for cast_list in [x['cast'] for x in all_films['credits']]])

actors_df = actors.apply(pd.Series) \
    .merge(all_films, left_index = True, right_index = True) \
    .melt(id_vars=['budget', 'credits', 'genres', 'id', 'original_language', 'popularity',
       'production_companies', 'production_countries', 'release_date',
       'revenue', 'runtime', 'spoken_languages', 'status', 'title',
       'vote_average', 'vote_count', 'year', 'decade', 'budget_adj',
       'revenue_adj', 'profit', 'profit_adj', 'budget_bin', 'budget_adj_bin',
       ], value_name='actor') \
    .drop(columns="variable") \
    .dropna(subset=['actor'])

actors_gender = pd.Series(
    [[x['gender'] for x in cast_list] 
        for cast_list in [x['cast'] for x in all_films['credits']]
    ])

actors_gender_df = actors_gender.apply(pd.Series) \
    .merge(all_films[['id']], left_index = True, right_index = True) \
    .melt(id_vars=['id'], value_name='gender') \
    .drop(columns="variable") \
    .dropna(subset=['gender'])

actors_df = actors_df.merge(actors_gender_df['gender'], 
                                left_index=True, right_index=True
                               ).drop(columns=['credits'])

actors_df['gender'].replace({0: 'Unspecified', 1: 'Female', 2: 'Male'}, inplace=True)

In [72]:
actors_rank = movies.rankings(actors_df, actor=True)

actors_rank_decades = movies.rankings_decades(actors_df, actor=True)

actors_rank_years = movies.rankings_years(actors_df, actor=True)

In [73]:
actors_rank.sort_values('profit_adj', ascending=False)[0:10]

actor  films    profit_adj    budget_adj  average_profit  \
69             Stan Lee     46  2.563551e+10  7.352560e+09    5.572936e+08   
0          Frank Welker    144  2.339032e+10  8.332286e+09    1.624328e+08   
1     Samuel L. Jackson    108  2.323661e+10  7.421424e+09    2.151538e+08   
478       Warwick Davis     28  1.550110e+10  3.589688e+09    5.536108e+08   
248   John Ratzenberger     35  1.494645e+10  4.333373e+09    4.270415e+08   
74       Mickie McGowan     45  1.436162e+10  4.761154e+09    3.191472e+08   
207        Jess Harnell     37  1.399615e+10  3.613452e+09    3.782743e+08   
70   Scarlett Johansson     46  1.364463e+10  3.652827e+09    2.966224e+08   
173         Sherry Lynn     39  1.283832e+10  4.257010e+09    3.291876e+08   
44    Robert Downey Jr.     50  1.233623e+10  3.900828e+09    2.467247e+08   

     profit_rank  budget_rank  average_profit_rank  gender  
69           1.0          3.0               3568.0    Male  
0            2.0          1.0              16019.0    Male  
1            3.0          2.0              12204.0    Male  
478          4.0         25.0               3583.0    Male  
248          5.0         10.0               5240.0    Male  
74           6.0          5.0               7843.0  Female  
207          7.0         24.0               6335.0    Male  
70           8.0         20.0               8737.0  Female  
173          9.0         11.0               7481.0  Female  
44          10.0         14.0              10716.0    Male

In [74]:
actors_rank.sort_values('profit_rank', ascending=False)[0:10]

actor  films    profit_adj    budget_adj  average_profit  \
3873   Nastassja Kinski      8 -2.461976e+08  3.619064e+08   -3.077470e+07   
12144    Maria Bonnevie      3 -2.189756e+08  3.148153e+08   -7.299185e+07   
5608        Randle Mell      6 -2.160520e+08  3.894150e+08   -3.600867e+07   
4344    Harry Treadaway      8 -2.110637e+08  3.519583e+08   -2.638297e+07   
6545     Claudette Mink      6 -2.090058e+08  3.951976e+08   -3.483429e+07   
6062       Rie Kugimiya      6 -2.086817e+08  2.639282e+08   -3.478029e+07   
1360       Sean Pertwee     16 -2.086675e+08  3.821262e+08   -1.304172e+07   
6987        Remo Girone      5 -2.016793e+08  3.037899e+08   -4.033585e+07   
27523    Marat Basharov      2 -2.005851e+08  2.046432e+08   -1.002925e+08   
28983   Argos MacCallum      2 -1.995510e+08  2.972877e+08   -9.977549e+07   

       profit_rank  budget_rank  average_profit_rank       gender  
3873      102487.0       4804.0              99381.0       Female  
12144     102486.0       5761.0             102035.0       Female  
5608      102485.0       4320.0             100052.0         Male  
4344      102484.0       5006.0              98593.0         Male  
6545      102483.0       4238.0              99921.0       Female  
6062      102482.0       7430.0              99899.0       Female  
1360      102481.0       4427.0              93357.0         Male  
6987      102480.0       6177.0             100598.0         Male  
27523     102479.0      10876.0             102378.0  Unspecified  
28983     102478.0       6344.0             102377.0         Male

In [75]:
actors_df[actors_df['actor'] == 'Frank Welker'][['title', 'actor']]

title         actor
3736                     Scooby-Doo! in Where's My Mummy?  Frank Welker
3778                Scooby-Doo! and the Loch Ness Monster  Frank Welker
3976                                    Aloha Scooby-Doo!  Frank Welker
4125                Scooby-Doo! and the Monster of Mexico  Frank Welker
5072                       Scooby-Doo! The Mystery Begins  Frank Welker
5155                                 Garfield's Pet Force  Frank Welker
5554                                   Garfield Gets Real  Frank Welker
6364                               Scooby-Doo! Camp Scare  Frank Welker
6942                             Scooby-Doo! Stage Fright  Frank Welker
12991                            Transformers: Beginnings  Frank Welker
13619                       Tom and Jerry: The Magic Ring  Frank Welker
13893           Scooby-Doo! and the Legend of the Vampire  Frank Welker
19260                         The Transformers: The Movie  Frank Welker
20352                   Scooby-Doo! and the Witch's Ghost  Frank Welker
22846                   Scooby-Doo and the Alien Invaders  Frank Welker
23721   The Land Before Time XII: The Great Day of the...  Frank Welker
25884                         Scooby-Doo! Abracadabra-Doo  Frank Welker
26513                    Scooby-Doo! WrestleMania Mystery  Frank Welker
39074                                             Aladdin  Frank Welker
47996                              The Chipmunk Adventure  Frank Welker
49000                                    Cats Don't Dance  Frank Welker
49218                           The Prince and the Pauper  Frank Welker
49438                               Belle's Magical World  Frank Welker
49776                                   Love Potion No. 9  Frank Welker
51997                                      Curious George  Frank Welker
60078                               The Road to El Dorado  Frank Welker
60140                     Scooby-Doo! and the Cyber Chase  Frank Welker
61942                           Jimmy Neutron: Boy Genius  Frank Welker
62788             Batman: The Dark Knight Returns, Part 2  Frank Welker
68397                     Aladdin and the King of Thieves  Frank Welker
...                                                   ...           ...
208962                Star Trek III: The Search for Spock  Frank Welker
210409                          Gremlins 2: The New Batch  Frank Welker
219822                                      City Slickers  Frank Welker
219950                                      Mars Attacks!  Frank Welker
220143  Teenage Mutant Ninja Turtles II: The Secret of...  Frank Welker
229392                                          MouseHunt  Frank Welker
232026                Transformers: Revenge of the Fallen  Frank Welker
232600                                               Igor  Frank Welker
261819                                         Big Hero 6  Frank Welker
264386                                         The Smurfs  Frank Welker
270058                       Looney Tunes: Back in Action  Frank Welker
277708                                              Shrek  Frank Welker
286577                                         The Shadow  Frank Welker
299738            Batman: The Dark Knight Returns, Part 1  Frank Welker
311514                                      Mirror Mirror  Frank Welker
314771                         Bill & Ted's Bogus Journey  Frank Welker
323837                                          Space Jam  Frank Welker
324595                                        Hudson Hawk  Frank Welker
329928                                Shrek Forever After  Frank Welker
337717                                            Tangled  Frank Welker
358500                     Transformers: Dark of the Moon  Frank Welker
390475                                   The Santa Clause  Frank Welker
400389                                            Species  Frank Welker
409750                                  The Rugrats Movie  Frank Welker
422913              

In [76]:
fig = px.scatter(actors_rank_years[actors_rank_years['profit_rank']<=50], 
                 x='year', y='profit_rank',
                 hover_data=['actor'], color='gender', size='profit_adj',
                 range_y=[51,-1], #color_discrete_sequence=px.colors.sequential.Cividis
                )
fig.show()

In [77]:
fig = px.scatter(actors_rank_decades[actors_rank_decades['profit_rank']<=10], 
                 x='decade', y='profit_rank',
                 hover_data=['actor'], color='gender', size='profit_adj',
                 range_y=[11,-1], #color_discrete_sequence=px.colors.sequential.Cividis
                )
fig.show()

# Extract production companies

In [218]:
all_films['production_companies'][0]

[{'id': 7965,
  'logo_path': None,
  'name': 'The Ladd Company',
  'origin_country': 'US'},
 {'id': 10214,
  'logo_path': None,
  'name': 'Embassy International Pictures',
  'origin_country': 'US'},
 {'id': 11670,
  'logo_path': None,
  'name': 'Producers Sales Organization (PSO)',
  'origin_country': ''},
 {'id': 218,
  'logo_path': None,
  'name': 'Rafran Cinematografica',
  'origin_country': ''},
 {'id': 68621,
  'logo_path': None,
  'name': 'St. Petersburg Clearwater Film Commission',
  'origin_country': ''}]

In [242]:
production_countries = pd.Series(
    [[x['name'] for x in companies_list] 
        for companies_list in all_films['production_countries']],
        name='production_countries').to_frame()

In [246]:
production_countries \
                 .merge(all_films, left_index = True, right_index = True)

production_countries_x  \
0                     [United States of America, Italy]   
1                                               [Italy]   
2                            [United States of America]   
3                            [United States of America]   
4                                              [Canada]   
5                                     [Belarus, Russia]   
6                            [United States of America]   
7            [United Kingdom, United States of America]   
8                                       [Japan, France]   
9                            [United States of America]   
10    [Germany, France, United Kingdom, United State...   
11           [United Kingdom, United States of America]   
12                                [Soviet Union, Italy]   
13           [United Kingdom, United States of America]   
14                                            [Germany]   
15                           [United States of America]   
16                                             [Poland]   
17                    [Japan, United States of America]   
18                                     [United Kingdom]   
19                           [United States of America]   
20                           [United States of America]   
21                           [United States of America]   
22                                              [Japan]   
23                                             [Russia]   
24                           [United States of America]   
25    [United States of America, Hong Kong, United K...   
26                                              [Japan]   
27                                              [Italy]   
28                           [United States of America]   
29                                              [Japan]   
...                                                 ...   
9446                         [United States of America]   
9447                                  [Germany, Canada]   
9448                         [United States of America]   
9449                     [Italy, Malta, United Kingdom]   
9450        [Canada, Germany, United States of America]   
9451                         [United States of America]   
9452                         [United States of America]   
9453                 [United States of America, Canada]   
9454                         [United States of America]   
9455            [Switzerland, United States of America]   
9456                           [Canada, United Kingdom]   
9457                         [United States of America]   
9458                             [France, Italy, Spain]   
9459                         [United States of America]   
9460                         [United States of America]   
9461                         [United States of America]   
9462                         [United States of America]   
9463                         [United States of America]   
9464                         [United States of America]   
9465                         [United States of America]   
9466                         [United States of America]   
9467                         [United States of America]   
9468                                                 []   
9469                         [United States of America]   
9470                         [United States of America]   
9471                         [United States of America]   
9472                         [United States of America]   
9473                         [United States of America]   
9474                         [United States of America]   
9475                         [United States of America]   

                                                  title      budget  \
0                           Once Upon a Time in America  20000000.0   
1                                       Cinema Paradiso   5000000.0   
2                               The Empire Strikes Back  18000000.0   
3                                    Dead Poets Society  16400000.0   
4                  

In [252]:
companies = pd.Series(
    [[x['name'] for x in companies_list] for companies_list in all_films['production_companies']],
    name='companies').to_frame()

companies_df = list_col_to_rows(companies \
                 .merge(all_films, left_index = True, right_index = True), 
                 'companies')

In [266]:
companies_df.groupby(['year','title'])['companies'].count()

year  title                                         
1980  Airplane!                                          1
      Alligator                                          1
      Altered States                                     1
      American Gigolo                                    1
      Antropophagus                                      2
      Any Which Way You Can                              2
      Atlantic City                                      6
      Bad Timing                                         2
      Battle Beyond the Stars                            1
      Breaker Morant                                     3
      Bronco Billy                                       2
      Brubaker                                           1
      Caddyshack                                         2
      Cannibal Holocaust                                 1
      Cheech & Chong's Next Movie                        1
      Christmas Evil                                     2
   

In [263]:
fig = px.scatter(companies_df.groupby(['year','title'])['companies'].count().reset_index(),
              x='year', y='companies')
fig.show()